# DPS to extract raster covars to ATL08 geodataframes
Paul Montesano, PhD

In [1]:
from maap.maap import MAAP
maap = MAAP("api.maap-project.org") # needs this b/c of maap-py bug

In [2]:
import sys
ICESAT2_BOREAL_REPO_PATH = '/projects/code/icesat2_boreal'               #'/projects/icesat2_boreal' # /projects/Developer/icesat2_boreal/lib
ICESAT2_BOREAL_LIB_PATH = ICESAT2_BOREAL_REPO_PATH + '/lib'
sys.path.append(ICESAT2_BOREAL_LIB_PATH)
#!pip install -U -r $ICESAT2_BOREAL_REPO_PATH/dps/requirements_main.txt

In [3]:
import geopandas as gpd
import pandas as pd

import datetime
import glob
import os
import json
import collections
import numpy as np
import sys
import s3fs
import matplotlib.pyplot as plt
sys.path.append(ICESAT2_BOREAL_LIB_PATH)
import maplib_folium
import ExtractUtils
from folium import TileLayer
print("Importing packages complete.")

NASA MAAP
Importing packages complete.


In [4]:
import importlib
import mosaiclib
importlib.reload(mosaiclib)

<module 'mosaiclib' from '/projects/code/icesat2_boreal/lib/mosaiclib.py'>

In [5]:
from mosaiclib import *

### Example extraction - tests will fail if tile is missing from an covar tindex master csv

In [7]:
import extract_atl08_covars
importlib.reload(extract_atl08_covars)

<module 'extract_atl08_covars' from '/projects/code/icesat2_boreal/lib/extract_atl08_covars.py'>

In [9]:
s3 = s3fs.S3FileSystem(anon=True)

In [10]:
TILE_TEST = 997
YEAR_TEST = '2021'
PADVAL = '06'
if YEAR_TEST == '2020': PADVAL = '05'
f_list = s3.glob(f"s3://maap-ops-workspace/montesano/data/process_atl08_boreal/030m/{YEAR_TEST}/*.parquet")
fn = f_list[100]
fn = f'maap-ops-workspace/montesano/data/process_atl08_boreal/030m/{YEAR_TEST}/atl08_006_030m_{YEAR_TEST}_{YEAR_TEST}_06_09_filt_{TILE_TEST:06}.parquet'
fn
#fn = f'maap-ops-workspace/montesano/data/process_atl08_boreal/030m/{YEAR_TEST}/atl08_006_030m_{YEAR_TEST}_{YEAR_TEST}_06_09_filt_45970.parquet'

'maap-ops-workspace/montesano/data/process_atl08_boreal/030m/2021/atl08_006_030m_2021_2021_06_09_filt_000997.parquet'

In [11]:
if False:
    # with SAR
    df = extract_atl08_covars.extract_atl08_covars("s3://"+fn, [TOPO_TINDEX_FN_DICT['c2020updated'], HLS_TINDEX_FN_DICT[YEAR_TEST], SAR_TINDEX_FN_DICT[YEAR_TEST] ], outdir=None, RETURN_DF=True)
if True:
    # without SAR
    df = extract_atl08_covars.extract_atl08_covars("s3://"+fn, [TOPO_TINDEX_FN_DICT['c2020updated'], HLS_TINDEX_FN_DICT[YEAR_TEST] ], outdir='/projects/my-public-bucket/local_output', RETURN_DF=True)

s3://maap-ops-workspace/montesano/data/process_atl08_boreal/030m/2021/atl08_006_030m_2021_2021_06_09_filt_000997.parquet
(1777, 42)
997
Output dir: /projects/my-public-bucket/local_output

Extracting values from 2 sets of raster stacks and appending as columns to atl08 geodataframe...
s3://maap-ops-workspace/shared/montesano/DPS_tile_lists/run_build_stack_topo/build_stack_v2023_2/CopernicusGLO30/Topo_tindex_master.csv

Getting stack fn from:  s3://maap-ops-workspace/shared/montesano/DPS_tile_lists/run_build_stack_topo/build_stack_v2023_2/CopernicusGLO30/Topo_tindex_master.csv
s3://maap-ops-workspace/montesano/dps_output/run_build_stack_topo/build_stack_v2023_2/CopernicusGLO30/2024/01/16/11/12/25/676663/CopernicusGLO30_997_cog_topo_stack.tif
	Extracting raster values from:  s3://maap-ops-workspace/montesano/dps_output/run_build_stack_topo/build_stack_v2023_2/CopernicusGLO30/2024/01/16/11/12/25/676663/CopernicusGLO30_997_cog_topo_stack.tif
	Reproject points to match raster...
	Getting ba

In [10]:
f"{TOPO_TINDEX_FN_DICT['c2020updated']+HLS_TINDEX_FN_DICT['2020']+SAR_TINDEX_FN_DICT['2020']}"

's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/run_build_stack_topo/build_stack_v2023_2/CopernicusGLO30/Topo_tindex_master.csvs3://maap-ops-workspace/shared/montesano/DPS_tile_lists/HLS/HLS_stack_2023_v1/HLS_H30_2020/HLS_tindex_master.csvs3://maap-ops-workspace/shared/montesano/DPS_tile_lists/run_build_stack/build_stack_v2023_2/build_stack_S1/SAR_S1_2020/S1_tindex_master.csv'

In [340]:
INFILE = DPS_FILE_LIST[-1]
# args = f"\
# -s3_atl08_gdf_fn {INFILE} \
# -tindex_fn_list {TOPO_TINDEX_FN_DICT['c2020updated']} {HLS_TINDEX_FN_DICT['2020']} {SAR_TINDEX_FN_DICT['2020']} \
# "
args = f"\
-s3_atl08_gdf_fn {INFILE} \
-tindex_fn_list {TOPO_TINDEX_FN_DICT['c2020updated']} {HLS_TINDEX_FN_DICT['2021']} \
"

In [341]:
!python /projects/code/icesat2_boreal/lib/extract_atl08_covars.py $args

NASA MAAP
s3://maap-ops-workspace/montesano/data/process_atl08_boreal/030m/2020/atl08_006_030m_2020_2020_06_09_filt_45970.parquet
(719, 42)
45970

Extracting values from 3 sets of raster stacks and appending as columns to atl08 geodataframe...
s3://maap-ops-workspace/shared/montesano/DPS_tile_lists/run_build_stack_topo/build_stack_v2023_2/CopernicusGLO30/Topo_tindex_master.csv

Getting stack fn from:  s3://maap-ops-workspace/shared/montesano/DPS_tile_lists/run_build_stack_topo/build_stack_v2023_2/CopernicusGLO30/Topo_tindex_master.csv
Traceback (most recent call last):
  File "/projects/code/icesat2_boreal/lib/extract_atl08_covars.py", line 85, in <module>
    main()
  File "/projects/code/icesat2_boreal/lib/extract_atl08_covars.py", line 82, in main
    extract_atl08_covars(args.s3_atl08_gdf_fn, args.tindex_fn_list, args.outdir, args.RETURN_DF, args.EXIT_IF_EMPTY)
  File "/projects/code/icesat2_boreal/lib/extract_atl08_covars.py", line 59, in extract_atl08_covars
    covar_fn = Covari

### Use MAAP Registration call in notebook chunk to register DPS algorithm
 - We need to register a DPS algorithm called `run_extract_covars` before proceeding to the chunks below...

In [174]:
maap.register_algorithm_from_yaml_file("/projects/code/icesat2_boreal/dps/registered/run_extract_atl08_covars.yml").text

'{"code": 200, "message": {"id": "62a49ac8646c79401720cbc8213fdb1c7bd51bfa", "short_id": "62a49ac8", "created_at": "2024-02-28T01:27:09.000+00:00", "parent_ids": ["e2e916647de12b62b6373163cee781ac36c21e53"], "title": "Registering algorithm: run_extract_atl08_covars", "message": "Registering algorithm: run_extract_atl08_covars", "author_name": "root", "author_email": "root@156a1941fa17", "authored_date": "2024-02-28T01:27:09.000+00:00", "committer_name": "root", "committer_email": "root@156a1941fa17", "committed_date": "2024-02-28T01:27:09.000+00:00", "trailers": {}, "web_url": "https://repo.maap-project.org/root/register-job-hysds-v4/-/commit/62a49ac8646c79401720cbc8213fdb1c7bd51bfa", "stats": {"additions": 0, "deletions": 0, "total": 0}, "status": "running", "project_id": 3, "last_pipeline": {"id": 12427, "iid": 843, "project_id": 3, "sha": "62a49ac8646c79401720cbc8213fdb1c7bd51bfa", "ref": "main", "status": "running", "source": "push", "created_at": "2024-02-28T01:27:10.163Z", "updat

## Run a DPS job across the list

In [12]:
# Boreal Tiles 
boreal_tiles_model_ready_fn = '/projects/shared-buckets/montesano/databank/boreal_tiles_v004_model_ready.gpkg'
boreal_tiles = gpd.read_file(boreal_tiles_model_ready_fn)

In [13]:
len(boreal_tiles)

4956

In [75]:
YEAR = '2023'
IDENTIFIER = f"{YEAR}"

In [76]:
s3 = s3fs.S3FileSystem(anon=True)

### Get inputs (`filtered ATL08 parquets`) and expected outputs (`filtered covars ATL08 parquets`)

In [77]:
def GET_EXPECTED_OUTPUT(YEAR, boreal_tiles):
    
    INPUT_FILE_LIST = ["s3://"+f for f in s3.glob(f"s3://maap-ops-workspace/montesano/data/process_atl08_boreal/030m/{YEAR}/**/*.parquet")]#[107:109]

    print(f"# of input filt ATL08 files (still needed from process_atl08_boreal()): {len(INPUT_FILE_LIST):>10} ({len(boreal_tiles)-len(INPUT_FILE_LIST)})\t ala: {os.path.basename(INPUT_FILE_LIST[0])}")

    EXPECTED_OUTPUT_FILE_LIST = []

    for INPUT_FILE in INPUT_FILE_LIST:
        TILE_NUM = int(INPUT_FILE.split('_')[-1].split('.')[0])
        if YEAR == 2020:
            EXPECTED_OUTPUT_FILE_LIST.append(os.path.basename(INPUT_FILE).split(f'_{TILE_NUM:05}.')[0] + f'_covars_{TILE_NUM:06}.parquet')
        else:
            EXPECTED_OUTPUT_FILE_LIST.append(os.path.basename(INPUT_FILE).split(f'_{TILE_NUM:06}.')[0] + f'_covars_{TILE_NUM:06}.parquet')

    print(f"# of EXPECTED output extracted covar filt ATL08 files: {len(EXPECTED_OUTPUT_FILE_LIST):>27}\t\t ala: {EXPECTED_OUTPUT_FILE_LIST[0]}")
    
    return INPUT_FILE_LIST, EXPECTED_OUTPUT_FILE_LIST

In [78]:
INPUT_FILE_LIST, EXPECTED_OUTPUT_FILE_LIST = GET_EXPECTED_OUTPUT(YEAR, boreal_tiles)

# of input filt ATL08 files (still needed from process_atl08_boreal()):       4956 (0)	 ala: atl08_006_030m_2023_2023_06_09_filt_000004.parquet
# of EXPECTED output extracted covar filt ATL08 files:                        4956		 ala: atl08_006_030m_2023_2023_06_09_filt_covars_000004.parquet


In [79]:
DPS_FILE_LIST = INPUT_FILE_LIST
print(DPS_FILE_LIST[0])
len(DPS_FILE_LIST)

s3://maap-ops-workspace/montesano/data/process_atl08_boreal/030m/2023/atl08_006_030m_2023_2023_06_09_filt_000004.parquet


4956

## Set list of Covariate Tindexes for year

In [86]:
in_param_dict = {
    's3_atl08_gdf_fn': '',
    #'tindex_fn_list': f"{TOPO_TINDEX_FN_DICT['c2020updated']} {HLS_TINDEX_FN_DICT[YEAR]} {SAR_TINDEX_FN_DICT[YEAR]}"
    'tindex_fn_list': f"{TOPO_TINDEX_FN_DICT['c2020updated']} {HLS_TINDEX_FN_DICT[YEAR]}"
 }
in_param_dict

{'s3_atl08_gdf_fn': '',
 'tindex_fn_list': 's3://maap-ops-workspace/shared/montesano/DPS_tile_lists/run_build_stack_topo/build_stack_v2023_2/CopernicusGLO30/Topo_tindex_master.csv s3://maap-ops-workspace/shared/montesano/DPS_tile_lists/HLS/HLS_stack_2023_v1/HLS_H30_2023/HLS_tindex_master.csv'}

In [87]:
# MAAP algorithm version name (same as the repo TAG)
MAAP_VERSION = "extract_atl08_covars" 

In [88]:
ALGO_ID = "run_extract_atl08_covars"
USER = 'montesano'
WORKER_TYPE = 'maap-dps-worker-8gb'

In [89]:
#DPS_FILE_LIST = ['s3://maap-ops-workspace/montesano/data/process_atl08_boreal/030m/2020/atl08_006_030m_2020_2020_06_09_filt_00167.parquet']
len(DPS_FILE_LIST)

1

In [90]:
%%time
submit_results_df_list = []
len_input_list = len(DPS_FILE_LIST)
print(f"# of input tiles for DPS: {len_input_list}")

for i, INPUT_FILE in enumerate(DPS_FILE_LIST):

    DPS_num = i+1
    
    in_param_dict['s3_atl08_gdf_fn'] = INPUT_FILE
    INPUT_TILE_NUM = int(INPUT_FILE.split('_')[-1].split('.')[0])
    
    submit_result = maap.submitJob(
                                    identifier=IDENTIFIER,
                                    algo_id=ALGO_ID,
                                    version=MAAP_VERSION, 
                                    username=USER,
                                    queue=WORKER_TYPE,
                                    # Args that match yaml
                                    **in_param_dict
        )
    
    # Build a dataframe of submission details
    submit_result_df = pd.DataFrame( 
        {
                'dps_num':[DPS_num],
                'tile_num':[INPUT_TILE_NUM],
                'submit_time':[datetime.datetime.now().strftime('%Y-%m-%d-%H-%M-%s')],
                'dbs_job_hour': [datetime.datetime.now().hour],
                'algo_id': [ALGO_ID],
                'user': [USER],
                'worker_type': [WORKER_TYPE],
                'job_id': [submit_result.id],
                'submit_status': [submit_result.status],
        } 
    )
    
    # Append to a list of data frames of submission results
    submit_results_df_list.append(submit_result_df)
    
    if DPS_num in [1, 5, 10, 50, 100, 250, 500, 750, 1000, 1500, 2000, 2500, 3000, 3500, 4000, 4500, 5000, 7000, 9000, 11000, 13000, 15000, 17000, 19000, 21000, 24000, len_input_list]:
        print(f"DPS run #: {DPS_num:05} | tile num: {INPUT_TILE_NUM:06} | submit status: {submit_result.status} | job id: {submit_result.id}") 
        
# Build a final submission results df and save
submit_results_df = pd.concat(submit_results_df_list)
submit_results_df['run_name'] = IDENTIFIER
nowtime = pd.Timestamp.now().strftime('%Y%m%d%H%M')
print(f"Current time:\t{nowtime}")
submit_results_df.to_csv(f'/projects/my-public-bucket/dps_submission_results/DPS_{ALGO_ID}_{IDENTIFIER}_submission_results_{len_input_list}_{nowtime}.csv')
submit_results_df.info()

# of input tiles for DPS: 1
DPS run #: 00001 | tile num: 000997 | submit status: success | job id: 17bf6321-cacf-43a5-98ec-3a3d5dcb0b53
Current time:	202404011936
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1 entries, 0 to 0
Data columns (total 10 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   dps_num        1 non-null      int64 
 1   tile_num       1 non-null      int64 
 2   submit_time    1 non-null      object
 3   dbs_job_hour   1 non-null      int64 
 4   algo_id        1 non-null      object
 5   user           1 non-null      object
 6   worker_type    1 non-null      object
 7   job_id         1 non-null      object
 8   submit_status  1 non-null      object
 9   run_name       1 non-null      object
dtypes: int64(3), object(7)
memory usage: 208.0+ bytes
CPU times: user 28.1 ms, sys: 15.6 ms, total: 43.7 ms
Wall time: 382 ms


After almost any DPS job, you have to assess what succeeded and failed. This involves:
1. building a table of job status based on job ids captured in the job_results_df from the DPS run chunk (this takes 40 mins for ~47k jobs) --> this tells you how many jobs failed
2. merging the job status table with the job results df --> this tells you which specific granules (or tile nums) failed
3. building another input list of granules for a follow-up DPS
## Assess DPS results
Build a table of job status based on job id - how many jobs failed?

In [91]:
LIST_SUBMISSIONS = sorted(glob.glob(f'/projects/my-public-bucket/dps_submission_results/DPS_{ALGO_ID}*_submission_results_*.csv'), key=ExtractUtils.func, reverse=True)
LIST_SUBMISSIONS[0:3]

['/projects/my-public-bucket/dps_submission_results/DPS_run_extract_atl08_covars_2023_submission_results_1_202404011936.csv',
 '/projects/my-public-bucket/dps_submission_results/DPS_run_extract_atl08_covars_2021_submission_results_43_202404011912.csv',
 '/projects/my-public-bucket/dps_submission_results/DPS_run_extract_atl08_covars_submission_results_job_status_43_202404011912.csv']

In [92]:
import ExtractUtils
importlib.reload(ExtractUtils)

NASA MAAP


<module 'ExtractUtils' from '/projects/code/icesat2_boreal/lib/ExtractUtils.py'>

In [100]:
%%time

running_list = []
fails_list = []
success_list = []
offline_list = []

for fn in LIST_SUBMISSIONS[0:1]:
    
    if not 'job_status' in fn:

        DPS_alg_id = os.path.basename(fn.split('_submission_results_')[0].replace('DPS_',''))
        thentime = fn.split('_')[-1].replace('.csv','')
        print(f'DPS alg:\t\t{DPS_alg_id}')
        print(f'DPS run name:\t\t{IDENTIFIER}')
        print(f'DPS launch time:\t{thentime}')

        # Build job status table
        df_jstatus = ExtractUtils.BUILD_TABLE_JOBSTATUS(pd.read_csv(fn))

        # Save job status table
        df_jstatus.to_csv(f'/projects/my-public-bucket/dps_submission_results/DPS_{ALGO_ID}_submission_results_job_status_{len(df_jstatus)}_{thentime}.csv')

        # Get current fails df and append to list
        df_jstatus['run_type'] = IDENTIFIER

        running_list.append(df_jstatus[ (df_jstatus['status'] == 'Running') ] )
        fails_list.append(  df_jstatus[ (df_jstatus['status'] == 'Failed') ] )
        success_list.append(df_jstatus[ (df_jstatus['status'] == 'Succeeded') ] )
        offline_list.append(df_jstatus[ (df_jstatus['status'] == 'Offline') ] )    
        
    df_all_running = pd.concat(running_list)          
    df_all_fails   = pd.concat(fails_list)
    df_all_success = pd.concat(success_list)
    df_all_offline = pd.concat(offline_list)

    print(f"Count offline jobs:\t{len(df_all_offline)}\n")  

DPS alg:		run_extract_atl08_covars_2023
DPS run name:		2023
DPS launch time:	202404011936
multiprocessing...
Count total jobs:	1
Count pending jobs:	0
Count running jobs:	0
Count succeeded jobs:	1
Count failed jobs:	0
% of failed jobs:	Nothing has failed...yet

Count offline jobs:	0

CPU times: user 46 ms, sys: 578 ms, total: 624 ms
Wall time: 857 ms


### Get new DPS_FILE_LIST from fails

In [235]:
# FAIL_LIST = df_all_fails.tile_num.to_list()
# DPS_FILE_LIST = []
# for TILE_NUM in FAIL_LIST:
#     DPS_FILE_LIST.append(["s3://"+f for f in s3.glob(f"s3://maap-ops-workspace/montesano/data/process_atl08_boreal/030m/{YEAR}/*{TILE_NUM:05}.parquet")][0])

# print(len(DPS_FILE_LIST))
# DPS_FILE_LIST[0]

### Get new DPS_FILE_LIST from EXPECTED and OUTPUT comparison

In [67]:
YEAR = 2023

In [82]:
INPUT_FILE_LIST, EXPECTED_OUTPUT_FILE_LIST = GET_EXPECTED_OUTPUT(YEAR, boreal_tiles)

# of input filt ATL08 files (still needed from process_atl08_boreal()):       4956 (0)	 ala: atl08_006_030m_2023_2023_06_09_filt_000004.parquet
# of EXPECTED output extracted covar filt ATL08 files:                        4956		 ala: atl08_006_030m_2023_2023_06_09_filt_covars_000004.parquet


In [83]:
SEARCH_STR = f"s3://maap-ops-workspace/montesano/dps_output/{ALGO_ID}/{MAAP_VERSION}/{IDENTIFIER}/**/*.parquet"
print(f"Extracting covariates for {YEAR} to files like this:\n\t{SEARCH_STR}")
OUT_PATH_LIST = s3.glob(SEARCH_STR)
OUTPUT_FILE_LIST = [os.path.basename(f) for f in OUT_PATH_LIST]
print(f"# of completed output files (unique): {len(OUTPUT_FILE_LIST):>20} ({len(list(set(OUTPUT_FILE_LIST)))})")
print(f"# of expected output files: {len(EXPECTED_OUTPUT_FILE_LIST):>30}")

DPS_FILE_LIST = []
TILE_NUM_LIST = []
for EXPECTED in EXPECTED_OUTPUT_FILE_LIST:
    if EXPECTED not in OUTPUT_FILE_LIST:
        TILE_NUM = int(EXPECTED.split('_')[-1].split('.')[0])
        if YEAR == '2020':
            need_tail =  f'_{TILE_NUM:05}.parquet'
        else:
            need_tail =  f'_{TILE_NUM:06}.parquet'
        NEED_TO_PROCESS = os.path.basename(EXPECTED).split(f'_covars_{TILE_NUM:06}')[0] + need_tail
        DPS_FILE_LIST.append(f"s3://maap-ops-workspace/montesano/data/process_atl08_boreal/030m/{YEAR}/{NEED_TO_PROCESS}")
        TILE_NUM_LIST.append(TILE_NUM)
print(f"# missing from expected, next DPS list: {len(DPS_FILE_LIST):>18}")  
print(f"# missing from boreal tiles v004 model ready set: {(len(boreal_tiles)-len(OUTPUT_FILE_LIST)):>8}")

Extracting covariates for 2023 to files like this:
	s3://maap-ops-workspace/montesano/dps_output/run_extract_atl08_covars/extract_atl08_covars/2023/**/*.parquet
# of completed output files (unique):                 4956 (4955)
# of expected output files:                           4956
# missing from expected, next DPS list:                  1
# missing from boreal tiles v004 model ready set:        0


In [84]:
len(DPS_FILE_LIST)

1

In [85]:
DPS_FILE_LIST

['s3://maap-ops-workspace/montesano/data/process_atl08_boreal/030m/2023/atl08_006_030m_2023_2023_06_09_filt_000997.parquet']

In [246]:
len(DPS_FILE_LIST)
z = gpd.read_parquet(DPS_FILE_LIST[0])
z.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
Index: 369 entries, 78895 to 82788
Data columns (total 42 columns):
 #   Column                Non-Null Count  Dtype   
---  ------                --------------  -----   
 0   extent_id             369 non-null    uint64  
 1   ph_count              369 non-null    uint32  
 2   solar_elevation       369 non-null    float32 
 3   snowcover             369 non-null    uint8   
 4   gnd_ph_count          369 non-null    uint32  
 5   h_canopy              369 non-null    float32 
 6   x_atc                 369 non-null    float64 
 7   h_mean_canopy         369 non-null    float32 
 8   h_min_canopy          369 non-null    float32 
 9   segment_id            369 non-null    uint32  
 10  spot                  369 non-null    uint8   
 11  h_te_median           369 non-null    float32 
 12  rgt                   369 non-null    uint16  
 13  veg_ph_count          369 non-null    uint32  
 14  cycle                 369 non-null    uint16  
 1

In [176]:
EXPECTED

'atl08_006_030m_2022_2022_06_09_filt_covars_4199500.parquet'

In [159]:
OUTPUT_FILE_LIST[0]

'atl08_006_030m_2022_2022_06_09_filt_covars_000062.parquet'

In [160]:
EXPECTED_OUTPUT_FILE_LIST[1]

'atl08_006_030m_2022_2022_06_09_filt_covars_000009.parquet'

## Map output for a tile

In [197]:
import maplib_folium

In [191]:
importlib.reload(maplib_folium)

<module 'maplib_folium' from '/projects/code/icesat2_boreal/lib/maplib_folium.py'>

In [43]:
FOCAL_TILE_NUM = 3030 #1200

In [45]:
atl08 = gpd.read_parquet('s3://' + OUT_PATH_LIST[FOCAL_TILE_NUM])
FOCAL_TILE = int(OUT_PATH_LIST[FOCAL_TILE_NUM].split('_')[-1].split('.')[0])

maplib_folium.map_tile_atl08(FOCAL_TILE, None, gpd.read_file(boreal_tile_index_path), 
                             ATL08_filt_tindex_master_fn = atl08,
                             DO_NIGHT=False,
                  map_width = 600, map_height=1200, OVERVIEW_MAP= True,
                  max_AGB_display = 50, max_AGBSE_display = 20
                 )

Input is dataframe

Num. of ATL08 obs. in tile 3109: 	5393
55.0112 -116.583


/projects/code/icesat2_boreal/lib/maplib_folium.py:690: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  location = (boreal_tile_of_interest_gdf.geometry.centroid.y, boreal_tile_of_interest_gdf.geometry.centroid.x),
/opt/conda/envs/pangeo/lib/python3.10/site-packages/folium/utilities.py:94: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  float(coord)
/opt/conda/envs/pangeo/lib/python3.10/site-packages/folium/utilities.py:100: FutureWarning: Calling float on a single element Series is deprecated and will raise a TypeError in the future. Use float(ser.iloc[0]) instead
  if math.isnan(float(coord)):
/opt/conda/envs/pangeo/lib/python3.10/site-packages/folium/utilities.py:102: FutureWarning: Calling float on a single element Series is deprecated and will raise

In [198]:
# import branca.colormap as cm
# pal_height_cmap = cm.LinearColormap(colors = ['black','#636363','#fc8d59','#fee08b','#ffffbf','#d9ef8b','#91cf60','#1a9850','pink','blue','purple'], vmin=0, vmax=30)
# pal_height_cmap.caption = 'Vegetation height from  ATL08 @ 30 m (h_can; rh98)'
# pal_height_cmap
#
#atl08.explore(column='h_canopy', cmap=pal_height_cmap, tiles=maplib_folium.tiler_basemap_image, attr=' ')